In [ ]:
!ssh-keygen -t rsa -b 4096 -C "alina.bodnya@yandex.ru"

Generating public/private rsa key pair.
Enter file in which to save the key (/root/.ssh/id_rsa): ^C


In [ ]:
!cat ~/.ssh/id_rsa.pub

ssh-rsa AAAAB3NzaC1yc2EAAAADAQABAAACAQCrDUj1eJ5P97TVRX9UsVEYRAqTr7TadhzZZ08qA/RHUIxKYOTYpKiieDA/0xkXACWox4PPyBhJXHTDuiK5lFMelT22zsCVWKpr9EBi5h11CBUliTik3S8fDWEpceAq370P6fOLVe9i5vrbHbD0dFet5k8mzJMBjpwdjKCnwD1xgPFNzRwa+hptvmbJZWPJtIcwf8ux0iDtx8JUCsnFfqzHTUynCpeq3ZBM6BF3+dB3wskEizj45KT4Z1eKBP0HQrFJujOZi8M7WswFklfD2mt9m/WMFo2kYZT13fhMAigKJyURObCFxtmCO1vSlC6A+iST5VvVW7ZUCqDyjuR+bmu7390pMSZj6+oXgUEWm6kKgpyOnc4VxAuhJAYrL9vA5BlwG2Oe/tzXCGkbxP9guAKMiDMYTK3/607yYUCDXu/fe8RPDxVfDmf5YHhSbJsoPRV5W9Me4FeWyvMWTDkBgmu7PSO+XC/0VgW35gIeljUm5TNgKuIlUaUaeWPJFuN/j3XCgbP/azhAMhTwnEAKqV8x9DjqJMKIA0ex1AaZwCvzjBsIjB3FYlIE2VJ2M7s395WvpqiNAZbjwhE+Fv0yu+Ohu3wm8SYYpGeBLy92USGP0oqZzQZqq+cGIVZy1SecCUZAHLnQ1A9F+YBBv0bjNPGRPEee+HI59X+4c3mkE5a3/Q== alina.bodnya@yandex.ru


In [ ]:
!ssh-keyscan github.com >> ~/.ssh/known_hosts

# github.com:22 SSH-2.0-c0d4cfa4
# github.com:22 SSH-2.0-c0d4cfa4
# github.com:22 SSH-2.0-c0d4cfa4
# github.com:22 SSH-2.0-c0d4cfa4
# github.com:22 SSH-2.0-c0d4cfa4


In [ ]:
!git clone git@github.com:hushchyn-mikhail/tabular_data_generation.git

Cloning into 'tabular_data_generation'...
remote: Enumerating objects: 6552, done.
remote: Counting objects: 100% (23/23), done.
remote: Compressing objects: 100% (17/17), done.
remote: Total 6552 (delta 11), reused 16 (delta 6), pack-reused 6529 (from 1)
Receiving objects: 100% (6552/6552), 1.03 GiB | 18.11 MiB/s, done.
Resolving deltas: 100% (1119/1119), done.
Updating files: 100% (2537/2537), done.


In [ ]:
%cd /content/tabular_data_generation/notebooks/TabSyn

/content/tabular_data_generation/notebooks/TabSyn


### Загрузим и обработаем датасет

In [ ]:
from  load_data import Load_Process_Dataset

D = Load_Process_Dataset('adult')
D.start_load()

Start processing dataset adult from UCI.
Finish downloading dataset from https://archive.ics.uci.edu/static/public/2/adult.zip, data has been saved to data/adult.
Finish unzipping adult.
adult (32561, 15) (16281, 15) (32561, 15)
Numerical (32561, 6)
Categorical (32561, 8)
Processing and Saving adult Successfully!
adult
Total 48842
Train 32561
Test 16281
Num 6
Cat 9


In [ ]:
LR = 1e-3
WD = 0
D_TOKEN = 4
TOKEN_BIAS = True

In [ ]:
N_HEAD = 1
FACTOR = 32
NUM_LAYERS = 2

In [ ]:
import torch
if torch.cuda.is_available():
    my_device = torch.device('cuda')
else:
    my_device = torch.device('cpu')
print('Device: {}'.format(my_device))

Device: cuda


## CVAE

### VAE

In [ ]:
!pip install wandb -qU

In [ ]:
# Log in to your W&B account
import wandb
import random
import math

In [ ]:
wandb.login()#f92e8d28a5700385183b7eb8fc6a93ab5e5440b6

<IPython.core.display.Javascript object>

wandb: Logging into wandb.ai. (Learn how to deploy a W&B server locally: https://wandb.me/wandb-server)
wandb: You can find your API key in your browser here: https://wandb.ai/authorize
wandb: Paste an API key from your profile and hit enter:

 ··········


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: No netrc file found, creating one.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc
wandb: Currently logged in as: alina-bodnya (alina-bodnya-hse) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


True

In [ ]:
wandb.init(
    # Set the project where this run will be logged
    project="diploma_TabSyn",
    # We pass a run name (otherwise it’ll be randomly assigned, like sunshine-lollypop-10)
    name=f"CVAE_1")

In [ ]:
import torch.nn as nn
import torch
import torch.nn.init as nn_init
import torch.nn.functional as F
from torch import Tensor
import typing as ty
import math

class Tokenizer(nn.Module):

    def __init__(self, d_numerical, categories, d_token, bias):
        super().__init__()
        if categories is None:
            d_bias = d_numerical
            self.category_offsets = None
            self.category_embeddings = None
        else:
            d_bias = d_numerical + len(categories)
            category_offsets = torch.tensor([0] + categories[:-1]).cumsum(0)
            self.register_buffer('category_offsets', category_offsets)
            self.category_embeddings = nn.Embedding(sum(categories), d_token)
            nn_init.kaiming_uniform_(self.category_embeddings.weight, a=math.sqrt(5))
            print(f'{self.category_embeddings.weight.shape=}')

        # take [CLS] token into account
        self.weight = nn.Parameter(Tensor(d_numerical + 1, d_token))
        self.bias = nn.Parameter(Tensor(d_bias, d_token)) if bias else None
        # The initialization is inspired by nn.Linear
        nn_init.kaiming_uniform_(self.weight, a=math.sqrt(5))
        if self.bias is not None:
            nn_init.kaiming_uniform_(self.bias, a=math.sqrt(5))

    @property
    def n_tokens(self):
        return len(self.weight) + (
            0 if self.category_offsets is None else len(self.category_offsets)
        )

    def forward(self, x_num, x_cat):
        x_some = x_num if x_cat is None else x_cat
        assert x_some is not None
        x_num = torch.cat(
            [torch.ones(len(x_some), 1, device=x_some.device)]  # [CLS]
            + ([] if x_num is None else [x_num]),
            dim=1,
        )

        x = self.weight[None] * x_num[:, :, None]

        if x_cat is not None:
            x = torch.cat(
                [x, self.category_embeddings(x_cat + self.category_offsets[None])],
                dim=1,
            )
        if self.bias is not None:
            bias = torch.cat(
                [
                    torch.zeros(1, self.bias.shape[1], device=x.device),
                    self.bias,
                ]
            )
            x = x + bias[None]

        return x.view(x.size(0), -1)


class LM(nn.Module):

    def __init__(
        self,
        dim: int
    ):
        super().__init__()

        self.Linear_1 = nn.Linear(dim, 128)
        self.Drop = nn.Dropout(p=0.2)
        self.ReLu1 = nn.ReLU()

        self.Linear_4 = nn.Linear(128, dim)
        self.Norm =nn.LayerNorm(dim, eps=1e-05, elementwise_affine=True)


    def forward(self, x):
        lin1 = self.Linear_1(x)
        dr = self.Drop(lin1)
        rel1 = self.ReLu1(dr)

        lin4 = self.Linear_4(rel1)
        norm = self.Norm(lin4)

        return norm

class VAE(nn.Module):
    def __init__(self, d_numerical, categories, num_layers, hid_dim, n_head = 1, factor = 4, bias = True):
        super(VAE, self).__init__()

        self.d_numerical = d_numerical
        self.categories = categories
        self.hid_dim = hid_dim
        d_token = hid_dim
       # self.n_head = n_head
        self.d_dim = self.d_numerical + len(self.categories)

        self.Tokenizer = Tokenizer(d_numerical, categories, d_token, bias = bias)#4 = d_token
        self.encoder_mu = LM(hid_dim*(self.d_dim+1))
        self.encoder_logvar = LM(hid_dim*(self.d_dim+1))

        self.decoder = LM(hid_dim*self.d_dim + self.d_numerical)

    def get_embedding(self, x):
        return self.encoder_mu(x, x).detach()

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5 * logvar)
        eps = torch.randn_like(std)
        return mu + eps * std

    def forward(self, x_num, x_cat):
        x = self.Tokenizer(x_num, x_cat)
        mu_z = self.encoder_mu(x)
        std_z = self.encoder_logvar(x)

        z = self.reparameterize(mu_z, std_z)

        z = z.view(z.size(0), self.d_dim+1, self.hid_dim)[:,1:]
        z = z.view(z.size(0), -1)
        h = self.decoder(torch.cat((z, x_num), dim=-1))

        return h, mu_z, std_z

class Reconstructor(nn.Module):
    def __init__(self, d_numerical, categories, d_token):
        super(Reconstructor, self).__init__()

        self.d_numerical = d_numerical
        self.categories = categories
        self.d_token = d_token

        # self.weight = nn.Parameter(Tensor(d_numerical, d_token))
        self.weight = nn.Parameter(Tensor(d_numerical, 1))
        nn.init.xavier_uniform_(self.weight, gain=1 / math.sqrt(2))
        self.cat_recons = nn.ModuleList()

        for d in categories:
            recon = nn.Linear(d_token, d)
            nn.init.xavier_uniform_(recon.weight, gain=1 / math.sqrt(2))
            self.cat_recons.append(recon)

    def forward(self, h, num):

        # h_num  = h[:, :self.d_numerical]
        h_cat  = h[:, self.d_numerical:]
        # recon_x_num = torch.mul(num, self.weight.unsqueeze(0)).sum(-1)
        recon_x_num = torch.mul(num.unsqueeze(-1), self.weight.unsqueeze(0)).sum(-1)
        recon_x_cat = []

        for i, recon in enumerate(self.cat_recons):

            recon_x_cat.append(recon(h_cat[:, i]))

        return recon_x_num, recon_x_cat

class Model_VAE(nn.Module):
    def __init__(self, num_layers, d_numerical, categories, d_token, n_head = 1, factor = 4,  bias = True):
        super(Model_VAE, self).__init__()
        self.d_numerical = d_numerical
        self.d_categories = len(categories)
        self.d_token = d_token

        self.VAE = VAE(d_numerical, categories, num_layers, d_token, n_head = n_head, factor = factor, bias = bias)
        self.Reconstructor = Reconstructor(d_numerical, categories, d_token)

    def get_embedding(self, x_num, x_cat):
        x = self.Tokenizer(x_num, x_cat)

        return self.VAE.get_embedding(x)

    def forward(self, x_num, x_cat):

        h, mu_z, std_z = self.VAE(x_num, x_cat)
        h_num = h[:, -self.d_numerical:]
        h = h[:, :-self.d_numerical]
        h = h.view(h.size(0), self.d_numerical + self.d_categories, self.d_token)
        # recon_x_num, recon_x_cat = self.Reconstructor(h[:, 1:])
        recon_x_num, recon_x_cat = self.Reconstructor(h, h_num)

        return recon_x_num, recon_x_cat, mu_z, std_z

class Encoder_model(nn.Module):
    def __init__(self, num_layers, d_numerical, categories, d_token, n_head, factor, bias = True):
        super(Encoder_model, self).__init__()
        self.d_numerical = d_numerical
        self.d_categories = len(categories)
        self.d_token = d_token

        self.Tokenizer = Tokenizer(d_numerical, categories, d_token, bias);#4
        self.VAE_Encoder = LM(d_token*(d_numerical + len(categories) + 1))

    def load_weights(self, Pretrained_VAE):
        self.Tokenizer.load_state_dict(Pretrained_VAE.VAE.Tokenizer.state_dict())
        self.VAE_Encoder.load_state_dict(Pretrained_VAE.VAE.encoder_mu.state_dict())

    def forward(self, x_num, x_cat):
        x = self.Tokenizer(x_num, x_cat)
        z = self.VAE_Encoder(x)
        z = z.view(z.size(0), self.d_numerical + self.d_categories + 1, self.d_token)
        return z, x_num

class Decoder_model(nn.Module):
    def __init__(self, num_layers, d_numerical, categories, d_token, n_head, factor, x_num, bias = True):
        super(Decoder_model, self).__init__()
        self.d_numerical = d_numerical
        self.d_categories = len(categories)
        self.d_token = d_token
        self.x_num = x_num
        self.VAE_Decoder = LM(d_token*(d_numerical + len(categories))+d_numerical)
        self.Detokenizer = Reconstructor(d_numerical, categories, d_token)

    def load_weights(self, Pretrained_VAE):
        self.VAE_Decoder.load_state_dict(Pretrained_VAE.VAE.decoder.state_dict())
        self.Detokenizer.load_state_dict(Pretrained_VAE.Reconstructor.state_dict())

    def forward(self, z):
        z = z.view(z.size(0), -1)
        h = self.VAE_Decoder(torch.cat((z, self.x_num), dim=-1))
        h_num = h[:, -self.d_numerical:]
        h =  h[:, :-self.d_numerical]
        h = h.view(h.size(0), self.d_numerical + self.d_categories, self.d_token)
        x_hat_num, x_hat_cat = self.Detokenizer(h, h_num)
        return x_hat_num, x_hat_cat

### train

In [ ]:

from dataclasses import astuple, dataclass, replace
from typing import Any, Literal, Optional, Union, cast, Tuple, Dict, List
# from model_train.vae_fully_conn import Model_VAE, Encoder_model, Decoder_model
import numpy as np
import torch
import enum
from pathlib import Path
import os
import json

import hashlib
from collections import Counter
from copy import deepcopy
from dataclasses import astuple, dataclass, replace
from importlib.resources import path
from pathlib import Path
from typing import Any, Literal, Optional, Union, cast, Tuple, Dict, List
from torch.utils.data import DataLoader
from torch.optim.lr_scheduler import ReduceLROnPlateau
from tqdm import tqdm
import time
import hashlib
import torch.nn as nn
import transform_data
from transform_data import transform_dataset, preprocess, TabularDataset
import wandb
def compute_loss(X_num, X_cat, Recon_X_num, Recon_X_cat, mu_z, logvar_z):
    ce_loss_fn = nn.CrossEntropyLoss()
    mse_loss = (X_num - Recon_X_num).pow(2).mean()
    ce_loss = 0
    acc = 0
    total_num = 0

    for idx, x_cat in enumerate(Recon_X_cat):
        if x_cat is not None:
            ce_loss += ce_loss_fn(x_cat, X_cat[:, idx])
            x_hat = x_cat.argmax(dim = -1)
        acc += (x_hat == X_cat[:,idx]).float().sum()
        total_num += x_hat.shape[0]

    ce_loss /= (idx + 1)
    acc /= total_num
    # loss = mse_loss + ce_loss

    temp = 1 + logvar_z - mu_z.pow(2) - logvar_z.exp()

    loss_kld = -0.5 * torch.mean(temp.mean(-1).mean())
    return mse_loss, ce_loss, loss_kld, acc



class VAE_main():
    def __init__(self, name, LR, WD, D_TOKEN, N_HEAD, FACTOR, NUM_LAYERS):
        super(VAE_main, self).__init__()
        self.name = name
        self.LR = LR
        self.WD = WD
        self.D_TOKEN = D_TOKEN
        self.N_HEAD = N_HEAD
        self.FACTOR = FACTOR
        self.NUM_LAYERS = NUM_LAYERS

    def tabsyn_vae_main(self, dataname = 'adult', ckpt_dir='model', max_beta=1e-2, min_beta=1e-5, lambd=0.7, device = 'cpu', num_epochs = 10):
        l_num_loss=[]
        l_cat_loss=[]
        l_kl_loss=[]
        l_val_mse_loss =[]
        l_val_ce_loss =[]
        l_train_acc =[]
        l_val_acc =[]
        l_val_kl_loss = []
        data_dir = f'data/{dataname}'

        ckpt_dir = f'{ckpt_dir}/{dataname}'
        if not os.path.exists(ckpt_dir):
            os.makedirs(ckpt_dir)

        model_save_path = f'{ckpt_dir}/model.pt'
        encoder_save_path = f'{ckpt_dir}/encoder.pt'
        decoder_save_path = f'{ckpt_dir}/decoder.pt'

        X_num, X_cat, categories, d_numerical = preprocess(data_dir)

        X_train_num, _ = X_num
        X_train_cat, _ = X_cat

        X_train_num, X_test_num = X_num
        X_train_cat, X_test_cat = X_cat

        X_train_num, X_test_num = torch.tensor(X_train_num).float(), torch.tensor(X_test_num).float()
        X_train_cat, X_test_cat =  torch.tensor(X_train_cat), torch.tensor(X_test_cat)


        train_data = TabularDataset(X_train_num.float(), X_train_cat)

        X_test_num = X_test_num.float().to(device)
        X_test_cat = X_test_cat.to(device)

        batch_size = 4096
        train_loader = DataLoader(
            train_data,
            batch_size = batch_size,
            shuffle = True,
            num_workers = 4,
        )

        model = Model_VAE(self.NUM_LAYERS, d_numerical, categories, self.D_TOKEN, n_head = self.N_HEAD, factor = self.FACTOR, bias = True)
        model = model.to(device)

        pre_encoder = Encoder_model(self.NUM_LAYERS, d_numerical, categories, self.D_TOKEN, n_head = self.N_HEAD, factor = self.FACTOR).to(device)
        pre_decoder = Decoder_model(self.NUM_LAYERS, d_numerical, categories, self.D_TOKEN, n_head = self.N_HEAD, factor = self.FACTOR, x_num = X_num).to(device)

        pre_encoder.eval()
        pre_decoder.eval()

        optimizer = torch.optim.Adam(model.parameters(), lr=self.LR, weight_decay=self.WD)
        scheduler = ReduceLROnPlateau(optimizer, mode='min', factor=0.95, patience=10, verbose=True)

        # num_epochs = 10
        best_train_loss = float('inf')

        current_lr = optimizer.param_groups[0]['lr']
        patience = 0

        beta = max_beta
        start_time = time.time()
        for epoch in range(num_epochs):
            # pbar = tqdm(train_loader, total=len(train_loader))
            # pbar.set_description(f"Epoch {epoch+1}/{num_epochs}")

            curr_loss_multi = 0.0
            curr_loss_gauss = 0.0
            curr_loss_kl = 0.0

            curr_count = 0

            for batch_num, batch_cat in train_loader:#pbar
                model.train()
                optimizer.zero_grad()

                batch_num = batch_num.to(device)
                batch_cat = batch_cat.to(device)

                Recon_X_num, Recon_X_cat, mu_z, std_z = model(batch_num, batch_cat)

                loss_mse, loss_ce, loss_kld, train_acc = compute_loss(batch_num, batch_cat, Recon_X_num, Recon_X_cat, mu_z, std_z)

                loss = loss_mse + loss_ce + beta * loss_kld
                loss.backward()
                optimizer.step()

                batch_length = batch_num.shape[0]
                curr_count += batch_length
                curr_loss_multi += loss_ce.item() * batch_length
                curr_loss_gauss += loss_mse.item() * batch_length
                curr_loss_kl    += loss_kld.item() * batch_length

            num_loss = curr_loss_gauss / curr_count
            cat_loss = curr_loss_multi / curr_count
            kl_loss = curr_loss_kl / curr_count


            '''
                Evaluation
            '''
            model.eval()
            with torch.no_grad():
                Recon_X_num, Recon_X_cat, mu_z, std_z = model(X_test_num, X_test_cat)

                val_mse_loss, val_ce_loss, val_kl_loss, val_acc = compute_loss(X_test_num, X_test_cat, Recon_X_num, Recon_X_cat, mu_z, std_z)
                val_loss = val_mse_loss.item() * 0 + val_ce_loss.item()

                scheduler.step(val_loss)
                new_lr = optimizer.param_groups[0]['lr']

                if new_lr != current_lr:
                    current_lr = new_lr
                    print(f"Learning rate updated: {current_lr}")

                train_loss = val_loss
                if train_loss < best_train_loss:
                    best_train_loss = train_loss
                    patience = 0
                    torch.save(model.state_dict(), model_save_path)
                else:
                    patience += 1
                    if patience == 10:
                        if beta > min_beta:
                            beta = beta * lambd
                l_num_loss.append(num_loss)
                l_cat_loss.append(cat_loss)
                l_kl_loss.append(kl_loss)
                l_val_mse_loss.append(val_mse_loss.item())
                l_val_ce_loss.append(val_ce_loss.item())
                l_train_acc.append(train_acc.item())
                l_val_acc.append(val_acc.item())
                l_val_kl_loss.append(val_kl_loss.item())
            wandb.log({"val_loss": val_loss, "Train MSE": num_loss, "Train CE":cat_loss, "Train KL":kl_loss,"Val CE":val_ce_loss.item(),"Val MSE":val_mse_loss.item(),
                    "Train ACC": train_acc.item(), "Val ACC":val_acc.item()})
            if epoch%10 ==0:
                print('epoch: {}, beta = {:.6f}, Train MSE: {:.6f}, Train CE:{:.6f}, Train KL:{:.6f}, Val MSE:{:.6f}, Val CE:{:.6f}, Train ACC:{:6f}, Val ACC:{:6f}'.format(epoch, beta, num_loss, cat_loss, kl_loss, val_mse_loss.item(), val_ce_loss.item(), train_acc.item(), val_acc.item() ))

        end_time = time.time()
        print('Training time: {:.4f} mins'.format((end_time - start_time)/60))

        # Saving latent embeddings
        with torch.no_grad():
            pre_encoder.load_weights(model)
            pre_decoder.load_weights(model)

            torch.save(pre_encoder.state_dict(), encoder_save_path)
            torch.save(pre_decoder.state_dict(), decoder_save_path)

            X_train_num = X_train_num.to(device)
            X_train_cat = X_train_cat.to(device)

            print('Successfully load and save the model!')

            train_z, cond = pre_encoder(X_train_num, X_train_cat)#.detach().cpu().numpy()
            np.save(f'{ckpt_dir}/cond.npy', cond.detach().cpu().numpy())
            np.save(f'{ckpt_dir}/train_z.npy', train_z.detach().cpu().numpy())

            print('Successfully save pretrained embeddings in disk!')


In [ ]:
# from model_train.train_vae_fully_conn import VAE_main
vae_train = VAE_main(name = 'adult', LR = 1e-3, WD = 0, D_TOKEN =4, N_HEAD = 1, FACTOR = 32, NUM_LAYERS = 2)

In [ ]:
vae_train.tabsyn_vae_main(device = my_device, ckpt_dir = 'model_fully', num_epochs = 4000)

No NaNs in numerical features, skipping
self.category_embeddings.weight.shape=torch.Size([104, 4])
self.category_embeddings.weight.shape=torch.Size([104, 4])


/usr/local/lib/python3.11/dist-packages/torch/utils/data/dataloader.py:624: UserWarning: This DataLoader will create 4 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/torch/optim/lr_scheduler.py:62: UserWarning: The verbose parameter is deprecated. Please use get_last_lr() to access the learning rate.
  warnings.warn(


epoch: 0, beta = 0.010000, Train MSE: 6.719365, Train CE:2.012738, Train KL:0.793761, Val MSE:4.816022, Val CE:1.888719, Train ACC:0.301620, Val ACC:0.314934
epoch: 10, beta = 0.010000, Train MSE: 2.200653, Train CE:1.749788, Train KL:1.194133, Val MSE:2.019817, Val CE:1.728044, Train ACC:0.517385, Val ACC:0.519351
epoch: 20, beta = 0.010000, Train MSE: 1.164055, Train CE:1.416454, Train KL:0.962582, Val MSE:1.058373, Val CE:1.387949, Train ACC:0.631011, Val ACC:0.631697
epoch: 30, beta = 0.010000, Train MSE: 0.565849, Train CE:1.117267, Train KL:0.882647, Val MSE:0.489682, Val CE:1.089380, Train ACC:0.701123, Val ACC:0.713197
epoch: 40, beta = 0.010000, Train MSE: 0.279502, Train CE:0.882402, Train KL:0.866989, Val MSE:0.214592, Val CE:0.842579, Train ACC:0.771206, Val ACC:0.786957
epoch: 50, beta = 0.010000, Train MSE: 0.160783, Train CE:0.696020, Train KL:0.877518, Val MSE:0.101619, Val CE:0.647391, Train ACC:0.810948, Val ACC:0.826874
epoch: 60, beta = 0.010000, Train MSE: 0.109968

In [ ]:
wandb.finish()

In [ ]:
from model_train.train_tabsyn import tabsyn_main
tabsyn_main(my_device, 'adult', 'model_fully', 10000)

model_fully/adult
MLPDiffusion(
  (proj): Linear(in_features=60, out_features=1024, bias=True)
  (mlp): Sequential(
    (0): Linear(in_features=1024, out_features=2048, bias=True)
    (1): SiLU()
    (2): Linear(in_features=2048, out_features=2048, bias=True)
    (3): SiLU()
    (4): Linear(in_features=2048, out_features=1024, bias=True)
    (5): SiLU()
    (6): Linear(in_features=1024, out_features=60, bias=True)
  )
  (map_noise): PositionalEmbedding()
  (time_embed): Sequential(
    (0): Linear(in_features=1024, out_features=1024, bias=True)
    (1): SiLU()
    (2): Linear(in_features=1024, out_features=1024, bias=True)
  )
)
the number of parameters 10616892
Epoch:0, Loss:0.7008958181077383
Epoch:100, Loss:0.2060378385084032
Epoch:200, Loss:0.7695601990520872
Epoch:300, Loss:0.7660936078712317
Epoch:400, Loss:0.7712105279333311
Epoch:500, Loss:0.7707205199151165
Epoch:600, Loss:0.7678237613188151
Early stopping
Time:  599.6687667369843


In [ ]:
import torch
import pandas as pd
import argparse
import warnings
import time
import json
import numpy as np
import os

from model_train.train_tabsyn import MLPDiffusion, Model
# from model_train.train_vae_fully_conn import Decoder_model
from transform_data import preprocess
def get_input_generate(dataname, model):
    # dataname = args.dataname

    curr_dir = 'tabsyn'#os.path.dirname(os.path.abspath(__file__))
    dataset_dir = f'data/{dataname}'
    ckpt_dir = f'{model}/{dataname}'

    with open(f'{dataset_dir}/info.json', 'r') as f:
        info = json.load(f)

    task_type = info['task_type']


    # ckpt_dir = f'{curr_dir}/ckpt/{dataname}'

    _, _, categories, d_numerical, num_inverse, cat_inverse = preprocess(dataset_dir, task_type = task_type, inverse = True)

    embedding_save_path = f'{ckpt_dir}/train_z.npy'#f'{curr_dir}/vae/ckpt/{dataname}/train_z.npy'
    train_z = torch.tensor(np.load(embedding_save_path)).float()
    condition = torch.tensor(np.load(f'{ckpt_dir}/cond.npy')).float()
    train_z = train_z[:, 1:, :]

    B, num_tokens, token_dim = train_z.size()
    in_dim = num_tokens * token_dim

    train_z = train_z.view(B, in_dim)
    pre_decoder = Decoder_model(2, d_numerical, categories, 4, n_head = 1, factor = 32, x_num = condition)#тут поправить 1

    decoder_save_path = f'{ckpt_dir}/decoder.pt'#f'{curr_dir}/vae/ckpt/{dataname}/decoder.pt'
    pre_decoder.load_state_dict(torch.load(decoder_save_path))

    info['pre_decoder'] = pre_decoder
    info['token_dim'] = token_dim

    return train_z, curr_dir, dataset_dir, ckpt_dir, info, num_inverse, cat_inverse
randn_like=torch.randn_like

SIGMA_MIN=0.002
SIGMA_MAX=80
rho=7
S_churn= 1
S_min=0
S_max=float('inf')
S_noise=1
@torch.no_grad()
def split_num_cat_target(syn_data, info, num_inverse, cat_inverse, device):
    task_type = info['task_type']

    num_col_idx = info['num_col_idx']
    cat_col_idx = info['cat_col_idx']
    target_col_idx = info['target_col_idx']

    n_num_feat = len(num_col_idx)
    n_cat_feat = len(cat_col_idx)

    if task_type == 'regression':
        n_num_feat += len(target_col_idx)
    else:
        n_cat_feat += len(target_col_idx)


    pre_decoder = info['pre_decoder']
    token_dim = info['token_dim']

    syn_data = syn_data.reshape(syn_data.shape[0], -1, token_dim)

    norm_input = pre_decoder(torch.tensor(syn_data))
    x_hat_num, x_hat_cat = norm_input

    syn_cat = []
    for pred in x_hat_cat:
        syn_cat.append(pred.argmax(dim = -1))

    syn_num = x_hat_num.cpu().numpy()
    syn_cat = torch.stack(syn_cat).t().cpu().numpy()

    syn_num = num_inverse(syn_num)
    syn_cat = cat_inverse(syn_cat)

    if info['task_type'] == 'regression':
        syn_target = syn_num[:, :len(target_col_idx)]
        syn_num = syn_num[:, len(target_col_idx):]

    else:
        syn_target = syn_cat[:, :len(target_col_idx)]
        syn_cat = syn_cat[:, len(target_col_idx):]

    return syn_num, syn_cat, syn_target

def recover_data(syn_num, syn_cat, syn_target, info):

    num_col_idx = info['num_col_idx']
    cat_col_idx = info['cat_col_idx']
    target_col_idx = info['target_col_idx']


    idx_mapping = info['idx_mapping']
    idx_mapping = {int(key): value for key, value in idx_mapping.items()}

    syn_df = pd.DataFrame()

    if info['task_type'] == 'regression':
        for i in range(len(num_col_idx) + len(cat_col_idx) + len(target_col_idx)):
            if i in set(num_col_idx):
                syn_df[i] = syn_num[:, idx_mapping[i]]
            elif i in set(cat_col_idx):
                syn_df[i] = syn_cat[:, idx_mapping[i] - len(num_col_idx)]
            else:
                syn_df[i] = syn_target[:, idx_mapping[i] - len(num_col_idx) - len(cat_col_idx)]


    else:
        for i in range(len(num_col_idx) + len(cat_col_idx) + len(target_col_idx)):
            if i in set(num_col_idx):
                syn_df[i] = syn_num[:, idx_mapping[i]]
            elif i in set(cat_col_idx):
                syn_df[i] = syn_cat[:, idx_mapping[i] - len(num_col_idx)]
            else:
                syn_df[i] = syn_target[:, idx_mapping[i] - len(num_col_idx) - len(cat_col_idx)]

    return syn_df
def sample_step(net, num_steps, i, t_cur, t_next, x_next):

    x_cur = x_next
    # Increase noise temporarily.
    gamma = min(S_churn / num_steps, np.sqrt(2) - 1) if S_min <= t_cur <= S_max else 0
    t_hat = net.round_sigma(t_cur + gamma * t_cur)
    x_hat = x_cur + (t_hat ** 2 - t_cur ** 2).sqrt() * S_noise * randn_like(x_cur)
    # Euler step.

    denoised = net(x_hat, t_hat).to(torch.float32)
    d_cur = (x_hat - denoised) / t_hat
    x_next = x_hat + (t_next - t_hat) * d_cur

    # Apply 2nd order correction.
    if i < num_steps - 1:
        denoised = net(x_next, t_next).to(torch.float32)
        d_prime = (x_next - denoised) / t_next
        x_next = x_hat + (t_next - t_hat) * (0.5 * d_cur + 0.5 * d_prime)

    return x_next

def sample(net, num_samples, dim, num_steps = 50, device = 'cuda:0'):
    latents = torch.randn([num_samples, dim], device=device)

    step_indices = torch.arange(num_steps, dtype=torch.float32, device=latents.device)

    sigma_min = max(SIGMA_MIN, net.sigma_min)
    sigma_max = min(SIGMA_MAX, net.sigma_max)

    t_steps = (sigma_max ** (1 / rho) + step_indices / (num_steps - 1) * (
                sigma_min ** (1 / rho) - sigma_max ** (1 / rho))) ** rho
    t_steps = torch.cat([net.round_sigma(t_steps), torch.zeros_like(t_steps[:1])])

    x_next = latents.to(torch.float32) * t_steps[0]

    with torch.no_grad():
        for i, (t_cur, t_next) in enumerate(zip(t_steps[:-1], t_steps[1:])):
            x_next = sample_step(net, num_steps, i, t_cur, t_next, x_next)

    return x_next

def sample_main(dataname = 'adult', model = 'model', device = 'cuda', steps = None):
    # dataname = args.dataname
    # device = args.device
    # steps = args.steps
    save_path = f'synthetic/{model}/{dataname}/synthetic.csv'
    if not os.path.exists(f'synthetic/{model}/{dataname}/'):
      os.makedirs(f'synthetic/{model}/{dataname}/')
    train_z, _, _, ckpt_path, info, num_inverse, cat_inverse = get_input_generate(dataname, model)
    in_dim = train_z.shape[1]

    mean = train_z.mean(0)

    denoise_fn = MLPDiffusion(in_dim, 1024).to(device)

    model = Model(denoise_fn = denoise_fn, hid_dim = train_z.shape[1]).to(device)
    print(ckpt_path)
    model.load_state_dict(torch.load(f'{ckpt_path}/model.pt'))

    '''
        Generating samples
    '''
    start_time = time.time()

    num_samples = train_z.shape[0]
    sample_dim = in_dim

    x_next = sample(model.denoise_fn_D, num_samples, sample_dim)
    x_next = x_next * 2 + mean.to(device)

    syn_data = x_next.float().cpu().numpy()
    syn_num, syn_cat, syn_target = split_num_cat_target(syn_data, info, num_inverse, cat_inverse, device)

    syn_df = recover_data(syn_num, syn_cat, syn_target, info)

    idx_name_mapping = info['idx_name_mapping']
    idx_name_mapping = {int(key): value for key, value in idx_name_mapping.items()}
    # if not os.path.exists(f'sample'):
    #     os.makedirs(f'sample')
    syn_df.rename(columns = idx_name_mapping, inplace=True)
    syn_df.to_csv(save_path, index = False)

    end_time = time.time()
    print('Time:', end_time - start_time)

    print('Saving sampled data to {}'.format(save_path))

In [ ]:
# from generate_synthetic import sample_main
sample_main('adult', 'model_fully')

No NaNs in numerical features, skipping
model_fully/adult
Time: 13.282533168792725
Saving sampled data to synthetic/model_fully/adult/synthetic.csv


In [ ]:
pip install prdc

In [ ]:
from metrics.mle import MLE

Синтетика

In [ ]:
dataname = 'adult'
model = 'model_fully'

train_path = f'synthetic/{model}/{dataname}/synthetic.csv'
test_path = f'synthetic/{dataname}/test.csv'
MLE(train_path, test_path, dataname, model = 'test')

  0%|          | 0/36 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:46:53] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:46:53] WARNING: /workspace/src/common/error_msg.cc:58: Falling back to prediction using DMatrix due to mismatched devices. This might lead to higher memory usage and slower performance. XGBoost is running on: cuda:0, while the input data is on: cpu.
Potential solutions:
- Use a data structure that matches the device ordinal in the booster.
- Set the device for booster before call to inplace_predict.

This warning will only be shown once.

  warnings.warn(smsg, UserWarning)
  3%|▎         | 1/36 [00:01<00:47,  1.36s/it]/usr/local/lib/python3.1

Saving scores to  eval/mle/adult/test.json


/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:47:12] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)


Трушные

In [ ]:
dataname = 'adult'
model = 'model_fully'
train_path = f'synthetic/{dataname}/real.csv'
test_path = f'synthetic/{dataname}/test.csv'

MLE(train_path, test_path, dataname, model = 'real')

  0%|          | 0/36 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:47:12] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
  3%|▎         | 1/36 [00:00<00:08,  4.33it/s]/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:47:13] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU training, set the `device` parameter to CUDA instead.

    E.g. tree_method = "hist", device = "cuda"

  warnings.warn(smsg, UserWarning)
  6%|▌         | 2/36 [00:00<00:09,  3.68it/s]/usr/local/lib/python3.11/dist-packages/xgboost/core.py:158: UserWarning: [20:47:13] WARNING: /workspace/src/common/error_msg.cc:27: The tree method `gpu_hist` is deprecated since 2.0.0. To use GPU 

Saving scores to  eval/mle/adult/real.json


In [ ]:
import json
import pandas as pd
with open('eval/mle/adult/test.json', 'r') as myFile:
    synthetic = json.load(myFile)

In [ ]:
with open('eval/mle/adult/real.json', 'r') as myFile:
    real = json.load(myFile)

In [ ]:
df_real = pd.DataFrame({key: value["XGBClassifier"] for key, value in real.items()})
df_synt = pd.DataFrame({key: value["XGBClassifier"] for key, value in synthetic.items()})

df_real = df_real.rename(index={key: f'{key}_real' for key in df_real.index})
df_synt = df_synt.rename(index={key: f'{key}_synt' for key in df_synt.index})

df = pd.concat([df_real, df_synt])
df.sort_index(inplace=True)

df

best_f1_scores  best_weighted_scores  best_auroc_scores  \
accuracy_real           0.871691              0.871691           0.874578   
accuracy_synt           0.838401              0.838401           0.832504   
binary_f1_real          0.704401              0.704401           0.709365   
binary_f1_synt          0.594545              0.594545           0.559664   
roc_auc_real            0.924659              0.924659           0.926815   
roc_auc_synt            0.884519              0.884519           0.880551   
weighted_f1_real        0.754873              0.754873           0.759131   
weighted_f1_synt        0.666486              0.666486           0.639253   

                  best_acc_scores  best_avg_scores  
accuracy_real            0.871691         0.872367  
accuracy_synt            0.834285         0.838401  
binary_f1_real           0.704401         0.707489  
binary_f1_synt           0.589220         0.594545  
roc_auc_real             0.924659         0.926762  
roc_auc_synt             0.883535         0.884519  
weighted_f1_real         0.754873         0.757306  
weighted_f1_synt         0.661739         0.666486

### Alpha Precision and Beta Recall

In [ ]:
pip install synthcity

In [ ]:
from metrics.alpha_beta import Alpha_Beta
Alpha_Beta(model = 'model_fully', syn_path = 'synthetic/model_fully/adult/synthetic.csv', real_path = f'synthetic/adult/real.csv',data_dir = f'data/adult',dataname = 'adult')


=========== All Features ===========
Data shape:  (32561, 110)
alpha precision: 0.984807, beta recall: 0.268735


In [ ]:
pip install sdmetrics

In [ ]:
import numpy as np
import pandas as pd
import os

import json

# Metrics
from sdmetrics.reports.single_table import QualityReport, DiagnosticReport


def reorder(real_data, syn_data, info):
    num_col_idx = info['num_col_idx']
    cat_col_idx = info['cat_col_idx']
    target_col_idx = info['target_col_idx']

    task_type = info['task_type']
    if task_type == 'regression':
        num_col_idx += target_col_idx
    else:
        cat_col_idx += target_col_idx

    real_num_data = real_data[num_col_idx]
    real_cat_data = real_data[cat_col_idx]

    new_real_data = pd.concat([real_num_data, real_cat_data], axis=1)
    new_real_data.columns = range(len(new_real_data.columns))

    syn_num_data = syn_data[num_col_idx]
    syn_cat_data = syn_data[cat_col_idx]

    new_syn_data = pd.concat([syn_num_data, syn_cat_data], axis=1)
    new_syn_data.columns = range(len(new_syn_data.columns))


    metadata = info['metadata']

    columns = metadata['columns']
    metadata['columns'] = {}

    inverse_idx_mapping = info['inverse_idx_mapping']


    for i in range(len(new_real_data.columns)):
        if i < len(num_col_idx):
            metadata['columns'][i] = columns[num_col_idx[i]]
        else:
            metadata['columns'][i] = columns[cat_col_idx[i-len(num_col_idx)]]


    return new_real_data, new_syn_data, metadata


In [ ]:
dataname = 'adult'
model = 'model'

# syn_path = 'synthetic/adult/synthetic.csv'

# real_path = f'synthetic/{dataname}/real.csv'
syn_path = 'synthetic/model_fully/adult/synthetic.csv'
real_path = f'synthetic/adult/real.csv'
data_dir = f'data/{dataname}'
print(syn_path)

with open(f'{data_dir}/info.json', 'r') as f:
    info = json.load(f)

syn_data = pd.read_csv(syn_path)
real_data = pd.read_csv(real_path)

save_dir = f'eval/density/{dataname}/{model}'
if not os.path.exists(save_dir):
    os.makedirs(save_dir)

real_data.columns = range(len(real_data.columns))
syn_data.columns = range(len(syn_data.columns))

metadata = info['metadata']
metadata['columns'] = {int(key): value for key, value in metadata['columns'].items()}

new_real_data, new_syn_data, metadata = reorder(real_data, syn_data, info)

qual_report = QualityReport()
qual_report.generate(new_real_data, new_syn_data, metadata)

diag_report = DiagnosticReport()
diag_report.generate(new_real_data, new_syn_data, metadata)

quality =  qual_report.get_properties()
diag = diag_report.get_properties()

Shape = quality['Score'][0]
Trend = quality['Score'][1]

with open(f'{save_dir}/quality.txt', 'w') as f:
    f.write(f'{Shape}\n')
    f.write(f'{Trend}\n')

Quality = (Shape + Trend) / 2

In [ ]:
shapes = qual_report.get_details(property_name='Column Shapes')
trends = qual_report.get_details(property_name='Column Pair Trends')
coverages_srt = diag_report.get_details('Data Structure')
coverages_val = diag_report.get_details('Data Validity')

In [ ]:
# pip install kaleido

In [ ]:
# pip install plotly==5.5.0

In [ ]:
import kaleido
import plotly

kaleido.__version__, plotly.__version__

In [ ]:
fig = qual_report.get_visualization(property_name='Column Shapes')
fig.show()
# fig.show(renderer = 'png')

In [ ]:
fig = qual_report.get_visualization(property_name='Column Pair Trends')
fig.show()
# fig.show(renderer = 'png')

In [ ]:
shapes = qual_report.get_details(property_name='Column Shapes')
trends = qual_report.get_details(property_name='Column Pair Trends')


print(f"Error rate (%) of column-wise density estimation : {(1 - shapes['Score'].mean())*100:.3f} ± {shapes['Score'].std()*100:.3f}")
print(f"Error rate (%) of pair-wise column correlation score : {(1 - trends['Score'].mean())*100:.3f} ± {trends['Score'].std()*100:.3f}")


Error rate (%) of column-wise density estimation : 1.894 ± 1.786
Error rate (%) of pair-wise column correlation score : 5.783 ± 6.304


In [ ]:
fig = diag_report.get_visualization(property_name = 'Data Validity')
fig.show()
# fig.show(renderer = 'png')

In [ ]:
from sdmetrics.visualization import get_column_plot
for i in range(0, 6):
    fig = get_column_plot(
        real_data=new_real_data,
        synthetic_data=new_syn_data,
        column_name= i,
        plot_type='distplot'
    )

    fig.show()
# fig.show(renderer = 'png')

In [ ]:
for i in range(6, 15):
    fig = get_column_plot(
        real_data=new_real_data,
        synthetic_data=new_syn_data,
        column_name= i,
        plot_type='bar'
    )

    fig.show()

### Pricavy protection: Distance to Closest Record (DCR)

In [ ]:
from metrics.dcr import DCR
DCR(dataname = 'adult', model = 'model_fully', syn_path = 'synthetic/model_fully/adult/synthetic.csv',
    real_path = f'synthetic/adult/real.csv',test_path = f'synthetic/adult/test.csv', data_dir = f'data/adult' )


DCR Score, a value closer to 0.5 is better
adult-model_fully, DCR Score = 0.6707717821934216


### Detection: Classifier Two Sample Tests (C2ST)

In [ ]:
from metrics.c2st import Detection
Detection(dataname = 'adult', model = 'model_fully', syn_path = 'synthetic/model_fully/adult/synthetic.csv',
    real_path = f'synthetic/adult/real.csv', data_dir = f'data/adult' )

adult, model_fully: 0.8898494621559486
